# Libraries

In [1]:
#!pip install -q catboost shap

In [2]:
import os 
#os.chdir("/content/drive/MyDrive/UmojaHack Africa 2023: Carbon Dioxide Prediction Challenge (BEGINNER)/Data")

In [3]:
import numpy as np
import pandas as pd

from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import train_test_split
from catboost import CatBoostRegressor
from catboost import Pool
from catboost import MetricVisualizer
import os
import matplotlib.pyplot as plt
import seaborn as sns
import shap
from collections import Counter

from sklearn.preprocessing import MinMaxScaler



import warnings
warnings.filterwarnings('ignore')
plt.style.use('fivethirtyeight')
%matplotlib inline

shap.initjs()

# Data

In [4]:
sorted(os.listdir("../Data"))

['SampleSubmission.csv', 'Test.csv', 'Train.csv', 'catboost_info']

In [5]:
ss, test, train = [pd.read_csv(f"../Data/{f}") for f in sorted(os.listdir("../Data"))[:3]]

# Basic EDA

In [6]:
ss.head(2)

ID_LAT_LON_YEAR_WEEK  emission
0  ID_-23.53_27.47_2019_1         0
1  ID_-23.53_27.47_2019_2         0

In [7]:
train.head(2)

ID_LAT_LON_YEAR_WEEK  latitude  longitude  year  week_no  \
0  ID_-23.73_28.77_2019_1    -23.73      28.77  2019        1   
1  ID_-23.73_28.77_2019_2    -23.73      28.77  2019        2   

   SulphurDioxide_SO2_column_number_density  \
0                                  0.000167   
1                                 -0.000155   

   SulphurDioxide_SO2_column_number_density_amf  \
0                                      0.713172   
1                                      0.812910   

   SulphurDioxide_SO2_slant_column_number_density  \
0                                        0.000102   
1                                       -0.000137   

   SulphurDioxide_cloud_fraction  SulphurDioxide_sensor_azimuth_angle  ...  \
0                       0.223929                            24.939440  ...   
1                       0.080281                            16.624162  ...   

   Cloud_cloud_top_height  Cloud_cloud_base_pressure  Cloud_cloud_base_height  \
0             5566.222019               54826.032616              4606.209995   
1             3711.511365               68491.753342              3034.461661   

   Cloud_cloud_optical_depth  Cloud_surface_albedo  \
0                  19.115282              0.353778   
1                  12.218664              0.244987   

   Cloud_sensor_azimuth_angle  Cloud_sensor_zenith_angle  \
0                   24.951948                  49.053953   
1                    4.708856                  42.586683   

   Cloud_solar_azimuth_angle  Cloud_solar_zenith_angle  emission  
0                 -89.638032                 17.988874  86.05170  
1                 -89.904314                 22.773246  88.87567  

[2 rows x 76 columns]

In [8]:
test.head(2)

ID_LAT_LON_YEAR_WEEK  latitude  longitude  year  week_no  \
0  ID_-23.53_27.47_2019_1    -23.53      27.47  2019        1   
1  ID_-23.53_27.47_2019_2    -23.53      27.47  2019        2   

   SulphurDioxide_SO2_column_number_density  \
0                                  0.000077   
1                                  0.000181   

   SulphurDioxide_SO2_column_number_density_amf  \
0                                      0.454468   
1                                      0.423171   

   SulphurDioxide_SO2_slant_column_number_density  \
0                                        0.000034   
1                                        0.000062   

   SulphurDioxide_cloud_fraction  SulphurDioxide_sensor_azimuth_angle  ...  \
0                       0.114291                           -80.286309  ...   
1                       0.075100                           -17.765690  ...   

   Cloud_cloud_top_pressure  Cloud_cloud_top_height  \
0              74897.052000             2180.266538   
1              84222.653521              982.619057   

   Cloud_cloud_base_pressure  Cloud_cloud_base_height  \
0               81287.074479              1562.031017   
1               90307.650011               927.111222   

   Cloud_cloud_optical_depth  Cloud_surface_albedo  \
0                  10.734123              0.280660   
1                   5.250020              0.238933   

   Cloud_sensor_azimuth_angle  Cloud_sensor_zenith_angle  \
0                  -31.230174                  33.337966   
1                   66.490898                  58.137794   

   Cloud_solar_azimuth_angle  Cloud_solar_zenith_angle  
0                 -93.217261                 23.358251  
1                 -85.001467                 13.416481  

[2 rows x 75 columns]

In [9]:
train.columns.difference(test.columns)

Index(['emission'], dtype='object')

# Splitting data

In [10]:
features = train.select_dtypes(["int", "float"]).columns.intersection(test.select_dtypes(["int", "float"]).columns).tolist()
features

['latitude',
 'longitude',
 'year',
 'week_no',
 'SulphurDioxide_SO2_column_number_density',
 'SulphurDioxide_SO2_column_number_density_amf',
 'SulphurDioxide_SO2_slant_column_number_density',
 'SulphurDioxide_cloud_fraction',
 'SulphurDioxide_sensor_azimuth_angle',
 'SulphurDioxide_sensor_zenith_angle',
 'SulphurDioxide_solar_azimuth_angle',
 'SulphurDioxide_solar_zenith_angle',
 'SulphurDioxide_SO2_column_number_density_15km',
 'CarbonMonoxide_CO_column_number_density',
 'CarbonMonoxide_H2O_column_number_density',
 'CarbonMonoxide_cloud_height',
 'CarbonMonoxide_sensor_altitude',
 'CarbonMonoxide_sensor_azimuth_angle',
 'CarbonMonoxide_sensor_zenith_angle',
 'CarbonMonoxide_solar_azimuth_angle',
 'CarbonMonoxide_solar_zenith_angle',
 'NitrogenDioxide_NO2_column_number_density',
 'NitrogenDioxide_tropospheric_NO2_column_number_density',
 'NitrogenDioxide_stratospheric_NO2_column_number_density',
 'NitrogenDioxide_NO2_slant_column_number_density',
 'NitrogenDioxide_tropopause_pressure'

In [11]:
train[features].var()[train[features].var()<5e-8]

SulphurDioxide_SO2_slant_column_number_density             3.946017e-08
SulphurDioxide_SO2_column_number_density_15km              6.153494e-09
NitrogenDioxide_NO2_column_number_density                  2.386937e-09
NitrogenDioxide_tropospheric_NO2_column_number_density     2.467667e-09
NitrogenDioxide_stratospheric_NO2_column_number_density    3.879787e-11
NitrogenDioxide_NO2_slant_column_number_density            3.654368e-09
Formaldehyde_tropospheric_HCHO_column_number_density       9.329211e-09
Formaldehyde_HCHO_slant_column_number_density              7.980467e-09
dtype: float64

In [12]:
train[features].fillna(0, inplace=True)
test[features].fillna(0, inplace=True)

In [13]:
scaler = MinMaxScaler()
train[features] = scaler.fit_transform(train[features])
test[features] = scaler.transform(test[features])

In [14]:
# features = list(set(features).difference(train[features].var()[train[features].var()<5e-8].index.tolist()))
# features

In [15]:
target = "emission"

In [16]:
X, y = train[features].fillna(0), train[target]

In [17]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=0)

In [18]:
print("Number of samples in X_train dataset: ", X_train.shape) 
print("Number of samples in y_train dataset: ", y_train.shape) 
print("Number of samples in X_test dataset: ", X_test.shape) 
print("Number of samples in y_test dataset: ", y_test.shape)

Number of samples in X_train dataset:  (59204, 74)
Number of samples in y_train dataset:  (59204,)
Number of samples in X_test dataset:  (14801, 74)
Number of samples in y_test dataset:  (14801,)


In [19]:
train_pool = Pool(
    data=X_train, 
    label=y_train
)

# create validation_pool object
validation_pool = Pool(
    data=X_test, 
    label=y_test
)

# Train model

In [20]:
# pretty basic model, max_depth=10 give slightly better results
cbs = CatBoostRegressor(iterations=30000,
                         learning_rate=0.0012,
                         loss_function='RMSE',
                         max_depth=8, 
                         early_stopping_rounds=300,
                         task_type = "CPU",
                        #  cat_features = cat_features
                        )

# we are passing categorical features as parameters here
cbs.fit(
    train_pool,
    eval_set=validation_pool,
    verbose=1000,
    plot=False 
);

0:	learn: 53105.4837908	test: 50096.7346205	best: 50096.7346205 (0)	total: 140ms	remaining: 1h 9m 50s
1000:	learn: 21532.6703185	test: 20999.0909828	best: 20999.0909828 (1000)	total: 46.2s	remaining: 22m 17s
2000:	learn: 12698.9865628	test: 12746.9346099	best: 12746.9346099 (2000)	total: 1m 31s	remaining: 21m 23s
3000:	learn: 10221.5693046	test: 10490.8831476	best: 10490.8831476 (3000)	total: 2m 15s	remaining: 20m 15s
4000:	learn: 8510.1947472	test: 8896.0500687	best: 8896.0500687 (4000)	total: 2m 54s	remaining: 18m 54s
5000:	learn: 7432.1728075	test: 7872.1806153	best: 7872.1806153 (5000)	total: 3m 34s	remaining: 17m 51s
6000:	learn: 6663.2711030	test: 7120.2577284	best: 7120.2577284 (6000)	total: 4m 14s	remaining: 16m 56s
7000:	learn: 6056.5926787	test: 6536.8576125	best: 6536.8576125 (7000)	total: 4m 53s	remaining: 16m 4s
8000:	learn: 5583.3243489	test: 6096.9964601	best: 6096.9964601 (8000)	total: 5m 33s	remaining: 15m 15s
9000:	learn: 5178.1790025	test: 5731.4715230	best: 5731.471

# Assess model

In [21]:
test_predictions = cbs.predict(X_test).flatten()

# error = (test_predictions - y_test)

# plt.figure(figsize=(10,10))
# plt.scatter(y_test, 
#             test_predictions, 
#             c=error,
#             s=1.9,
#             cmap='hsv'
#             )
# plt.colorbar()
# plt.xlabel('True Values [emission]')
# plt.ylabel('Predictions [emission]')
# plt.axis('equal')
# plt.axis('square')
# plt.xlim([0, plt.xlim()[1]])
# plt.ylim([0, plt.ylim()[1]])
# plt.show()

In [22]:
# error = test_predictions - y_test
# # print(type(error))

# plt.figure(figsize=(10,10))
# plt.scatter(y_test, 
#             test_predictions, 
#             c=error,
#             s=2,
#             cmap='hsv',
#             )
# plt.colorbar()
# plt.xlabel('True Values [emission]')
# plt.ylabel('Predictions [emission]')
# plt.axis('equal')
# plt.axis('square')
# plt.xlim([0, 30000])
# plt.ylim([0, 30000])
# plt.show()

In [23]:
# plt.figure(figsize=(10,10))
# plt.hist2d(y_test, test_predictions, (500,500),cmap=plt.cm.jet)
# plt.colorbar()
# plt.xlim([0, 30000])
# plt.ylim([0, 30000])
# plt.show()

In [24]:
# plt.figure(figsize=(16,7))
# plt.hist(error, bins = 300, rwidth=0.9)
# plt.xlabel('Predictions Error [emission]')
# _ = plt.ylabel('Count')
# plt.xlim([-8000, 8000])
# plt.show()

In [25]:
# %%time

# importance_types = ['PredictionValuesChange',
#                     'LossFunctionChange'
#                    ]


# for importance_type in importance_types:
#     print(importance_type)
#     print(cbs.get_feature_importance(data=train_pool, 
#                                      type=importance_type))
#     print('\n\n\n\n')

In [26]:
# %%time

# import shap
# shap.initjs()

# shap_values = cbs.get_feature_importance(Pool(X_test, 
#                                               label=y_test,
#                                               # cat_features=cat_features
#                                               ), 
#                                          type="ShapValues")
# print(type(shap_values))

# expected_value = shap_values[0,-1]
# print(expected_value)

# shap_values = shap_values[:,:-1]

In [27]:
# shap.summary_plot(shap_values, X_test, max_display=X_test.shape[1])

In [28]:
# shap.dependence_plot(ind='longitude', 
#                      interaction_index='longitude',
#                      shap_values=shap_values, 
#                      features=X_test,  
#                      display_features=X_test)

In [29]:
# shap.dependence_plot(ind='latitude', 
#                      interaction_index='latitude',
#                      shap_values=shap_values, 
#                      features=X_test,  
#                      display_features=X_test)

In [30]:
# shap.initjs()
# shap.force_plot(expected_value, shap_values[:1000,:], X_test.iloc[:1000,:])

In [31]:
# shap.initjs()
# for i in range(20,30):
#     print('Sample', i, 'from the test set:')
#     display(shap.force_plot(expected_value, shap_values[i,:], X_test.iloc[i,:]))
#     print('Listed_price -------------------------------------->', y_test.iloc[i])
#     print('parameters:\n', X_test.iloc[i,:])
#     print('\n\n\n\n\n\n\n')

# Submission

In [32]:
ss["emission"] = cbs.predict(test[features].fillna(0))

In [33]:

ss.to_csv("../Submissions/sub4_cpu_feat_with_low_var_added_local_fillna0_normalized_hyp_300_8_00012.csv", index=False)

In [34]:
#from google.colab import files

In [35]:
#files.download("../Submissions/sub4_cpu_feat_with_low_var_added_locql_fillna0.csv")